In [24]:
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.layers import Dense, Flatten, Dropout
from tensorflow.keras.models import Model
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.applications import DenseNet121
from tensorflow.keras.regularizers import l2
from tensorflow.keras.callbacks import ReduceLROnPlateau
from tensorflow.keras.callbacks import EarlyStopping


In [28]:
# Parameters
IMAGE_SIZE = (224, 224)
BATCH_SIZE = 32
NUM_CLASSES = 3  # Whole and Group and Plant_part

train_dir2 = '/Users/Esther./Desktop/Capstone/train data' 
val_dir = '/Users/Esther./Desktop/Capstone/validation data'

# Data Augmentation
train_datagen = ImageDataGenerator(
    rescale=1./255, 
    rotation_range=30,  # Increase rotation
    width_shift_range=0.3,  # Increase width shift
    height_shift_range=0.3,  # Increase height shift
    shear_range=0.2,
    zoom_range=0.3,  # Increase zoom
    brightness_range=[0.7, 1.3],  # Adjust brightness
    horizontal_flip=True,
    fill_mode='nearest'
)


val_datagen = ImageDataGenerator(rescale=1./255)

# Load images for training and validation
train_generator = train_datagen.flow_from_directory(
    train_dir2,
    target_size=IMAGE_SIZE,
    batch_size=BATCH_SIZE,
    class_mode='categorical'
)

validation_generator = val_datagen.flow_from_directory(
    val_dir,
    target_size=IMAGE_SIZE,
    batch_size=BATCH_SIZE,
    class_mode='categorical'
)

# Load the pre-trained DenseNet169 model without the top layer
base_model = DenseNet121(weights='imagenet', include_top=False, input_shape=(224, 224, 3))

# Freeze the base model

for layer in base_model.layers[:-30]:
    layer.trainable = False
for layer in base_model.layers[-30:]:
    layer.trainable = True



# Add custom classification layers
x = base_model.output
x = Flatten()(x)  # Flatten the output layer to 1 dimension

x = Dense(256, activation='relu', kernel_regularizer=l2(0.0001))(x)
x = Dropout(0.5)(x)


predictions = Dense(NUM_CLASSES, activation='softmax')(x) 

# Define the full model
model = Model(inputs=base_model.input, outputs=predictions)

# Compile the model
model.compile(optimizer=Adam(learning_rate=0.0001), loss='categorical_crossentropy', metrics=['accuracy'])

reduce_lr = ReduceLROnPlateau(monitor='val_loss', factor=0.2, patience=2, min_lr=1e-7)
early_stopping = EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True)

# Train the model
history = model.fit(
    train_generator,
    epochs=10,
    batch_size=32,
    validation_data=validation_generator, 
    callbacks=[reduce_lr]
)

val_accuracy = history.history['val_accuracy']

print(f'Final Validation Accuracy: {val_accuracy[-1]:.2f}')

Found 1118 images belonging to 3 classes.
Found 161 images belonging to 3 classes.
Epoch 1/10
35/35 ━━━━━━━━━━━━━━━━━━━━ 59s 1s/step - accuracy: 0.7907 - loss: 0.9386 - val_accuracy: 0.8012 - val_loss: 0.6894 - learning_rate: 1.0000e-04
Epoch 2/10
35/35 ━━━━━━━━━━━━━━━━━━━━ 51s 1s/step - accuracy: 0.8388 - loss: 0.5725 - val_accuracy: 0.8509 - val_loss: 0.3895 - learning_rate: 1.0000e-04
Epoch 3/10
35/35 ━━━━━━━━━━━━━━━━━━━━ 52s 1s/step - accuracy: 0.8712 - loss: 0.4137 - val_accuracy: 0.8385 - val_loss: 0.5472 - learning_rate: 1.0000e-04
Epoch 4/10
35/35 ━━━━━━━━━━━━━━━━━━━━ 52s 1s/step - accuracy: 0.8792 - loss: 0.3869 - val_accuracy: 0.8509 - val_loss: 0.4203 - learning_rate: 1.0000e-04
Epoch 5/10
35/35 ━━━━━━━━━━━━━━━━━━━━ 54s 1s/step - accuracy: 0.8361 - loss: 0.5004 - val_accuracy: 0.8571 - val_loss: 0.4175 - learning_rate: 2.0000e-05
Epoch 6/10
35/35 ━━━━━━━━━━━━━━━━━━━━ 53s 1s/step - accuracy: 0.8847 - loss: 0.3359 - val_accuracy: 0.8944 - val_loss: 0.3663 - learning_rate: 2.00

In [5]:
model.save('whole_or_group_classifier.keras')

In [9]:
from tensorflow.keras.models import load_model
from tensorflow.keras.preprocessing import image
import numpy as np
import os
import shutil
from PIL import UnidentifiedImageError, ImageFile
import pandas as pd

save to three files

In [8]:
# Load the previously saved model
model = load_model('whole_or_group_classifier.keras')

def preprocess_image(img_path, target_size=(224, 224)):
    try:
        img = image.load_img(img_path, target_size=target_size)  # Load image and resize
        img_array = image.img_to_array(img)  # Convert to array
        img_array = np.expand_dims(img_array, axis=0)  # Add batch dimension
        img_array /= 255.  # Rescale the image
        return img_array
    except UnidentifiedImageError:
        print(f"Skipping truncated image: {img_path}")
        return None
    except Exception as e:
        print(f"Error processing image {img_path}: {e}")
        return None

image_dir = '/Users/Esther./Desktop/Capstone/Exported Photos'
whole_dir = '/Users/Esther./Desktop/Capstone/final categorization/whole'
group_dir = '/Users/Esther./Desktop/Capstone/final categorization/group'
part_dir = '/Users/Esther./Desktop/Capstone/final categorization/plant_part'


# Create directories if they don't exist
os.makedirs(whole_dir, exist_ok=True)
os.makedirs(group_dir, exist_ok=True)
os.makedirs(part_dir, exist_ok=True)

# Iterate through each image in the directory
for filename in os.listdir(image_dir):
    if filename.endswith(('.jpg', '.jpeg', '.png')):  # Ensure file is an image
        img_path = os.path.join(image_dir, filename)
        
        # Preprocess the image
        img = preprocess_image(img_path)
        
        # Make prediction (model will output a probability)
        if img is not None:
            prediction = model.predict(img)[0]  # Get softmax output
        
            # Classify as 'whole', 'group', or 'plant_part'
            predicted_class = np.argmax(prediction)  # Get the index of the highest probability
            
            if predicted_class == 0:
                shutil.move(img_path, os.path.join(group_dir, filename))  # Move to group folder
            elif predicted_class == 1:
                shutil.move(img_path, os.path.join(part_dir, filename))  # Move to plant_part folder
            else:
                shutil.move(img_path, os.path.join(whole_dir, filename))  # Move to group folder

print("All images have been categorized and moved to their respective folders.")

1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 69ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 67ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 67ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 69ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 69ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 69ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 112ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 69ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 69ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 69ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━

save to an excel file

In [13]:
# Load the previously saved model
model = load_model('whole_or_group_classifier.keras')

def preprocess_image(img_path, target_size=(224, 224)):
    try:
        img = image.load_img(img_path, target_size=target_size)
        img_array = image.img_to_array(img)
        img_array = np.expand_dims(img_array, axis=0)
        img_array /= 255.
        return img_array
    except Exception as e:
        print(f"Error processing image {img_path}: {e}")
        return None

image_dir = '/Users/Esther./Desktop/Capstone/Exported Photos'
whole_dir = '/Users/Esther./Desktop/Capstone/final categorization/whole'
group_dir = '/Users/Esther./Desktop/Capstone/final categorization/group'
part_dir = '/Users/Esther./Desktop/Capstone/final categorization/plant_part'

# Create directories if they don't exist
os.makedirs(whole_dir, exist_ok=True)
os.makedirs(group_dir, exist_ok=True)
os.makedirs(part_dir, exist_ok=True)

# List to hold image data and their categories
image_data = []

# Iterate through each image in the directory
for filename in os.listdir(image_dir):
    if filename.endswith(('.jpg', '.jpeg', '.png')):
        img_path = os.path.join(image_dir, filename)
        
        # Preprocess the image
        img = preprocess_image(img_path)
        
        # Make prediction (model will output probabilities for each class)
        if img is not None:
            prediction = model.predict(img)[0]
            predicted_class_index = np.argmax(prediction)
            
            # Map the index to class name
            classes = ['whole', 'group', 'plant_part']
            class_name = classes[predicted_class_index]
            
            # Store the result
            image_data.append({'Photo Name': filename, 'Class': class_name})
            
            # Move the image to the appropriate folder
            target_directory = {
                'whole': whole_dir,
                'group': group_dir,
                'plant_part': part_dir
            }[class_name]

            shutil.move(img_path, os.path.join(target_directory, filename))

# Create a DataFrame from the collected image data
df = pd.DataFrame(image_data)

# Save the DataFrame to an Excel file
excel_path = '/Users/Esther./Desktop/Capstone/updated_classification.xlsx'
df.to_excel(excel_path, index=False)

print("All images have been categorized, moved to their respective folders, and listed in an Excel file.")


1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━